In [1]:
import itertools
import librosa
import matplotlib.pyplot as plt
import numpy as np
import os
import pandas as pd
from scipy.stats import kurtosis
from scipy.stats import skew

In [2]:
def get_features(y, sr, n_fft=1024, hop_length=512):
    features = {}

    features['spectral_centroid'] = librosa.feature.spectral_centroid(y=y, sr=sr, n_fft=n_fft, hop_length=hop_length).ravel()
    features['spectral_rolloff'] = librosa.feature.spectral_rolloff(y=y, sr=sr, n_fft=n_fft, hop_length=hop_length).ravel()
    features['zero_crossing_rate'] = librosa.feature.zero_crossing_rate(y, frame_length=n_fft, hop_length=hop_length).ravel()
    features['rms'] = librosa.feature.rms(y=y, frame_length=n_fft, hop_length=hop_length).ravel()
    features['onset_strength'] = librosa.onset.onset_strength(y=y, sr=sr).ravel()
    features['spectral_contrast'] = librosa.feature.spectral_contrast(y=y, sr=sr).ravel()
    features['spectral_bandwidth'] = librosa.feature.spectral_bandwidth(y=y, sr=sr, n_fft=n_fft, hop_length=hop_length).ravel()
    features['spectral_flatness'] = librosa.feature.spectral_flatness(y=y, n_fft=n_fft, hop_length=hop_length).ravel()

    mfcc = librosa.feature.mfcc(y=y, n_fft = n_fft, hop_length = hop_length, n_mfcc=13)

    for index, v_mfcc in enumerate(mfcc):
        features['mfcc_{}'.format(index)] = v_mfcc.ravel()

    def get_moments(descriptors):
        result = {}

        for k, v in descriptors.items():
            result['{}_max'.format(k)] = np.max(v)
            result['{}_min'.format(k)] = np.min(v)
            result['{}_mean'.format(k)] = np.mean(v)
            result['{}_std'.format(k)] = np.std(v)
            result['{}_kurtosis'.format(k)] = kurtosis(v)
            result['{}_skew'.format(k)] = skew(v)

        return result

    additional_features = get_moments(features)
    additional_features['tempo'] = librosa.feature.tempo(y=y, sr=sr)[0]

    return additional_features

In [3]:
def process_genres_directory_files(genres_directory, genres):
    all_features = []

    for genre in genres:
        genre_directory = f'{genres_directory}/{genre}'

        for file in os.listdir(genre_directory):
            file_path = f"{genre_directory}/{file}"

            y, sr = librosa.load(file_path)

            features = get_features(y, sr)

            features['label'] = genre

            all_features.append(features)

    return all_features

In [4]:
genres_directory = './data/genres_original'

In [5]:
genres = ['metal', 'disco', 'classical', 'hiphop', 'jazz', 'country', 'pop', 'blues', 'reggae', 'rock']

In [6]:
%%time

all_features = process_genres_directory_files(genres_directory, genres)

CPU times: total: 10min 48s
Wall time: 11min 45s


In [7]:
all_features

[{'spectral_centroid_max': 5514.393296072955,
  'spectral_centroid_min': 1789.3665834994376,
  'spectral_centroid_mean': 3177.044738996557,
  'spectral_centroid_std': 550.514459706086,
  'spectral_centroid_kurtosis': 1.2768330257828788,
  'spectral_centroid_skew': 0.8512716674602049,
  'spectral_rolloff_max': 9905.2734375,
  'spectral_rolloff_min': 4005.17578125,
  'spectral_rolloff_mean': 6235.752496918503,
  'spectral_rolloff_std': 1316.8176397218972,
  'spectral_rolloff_kurtosis': -0.1811429612929012,
  'spectral_rolloff_skew': 0.7399457991690924,
  'zero_crossing_rate_max': 0.4345703125,
  'zero_crossing_rate_min': 0.0341796875,
  'zero_crossing_rate_mean': 0.18303485112142304,
  'zero_crossing_rate_std': 0.05305270052176107,
  'zero_crossing_rate_kurtosis': 0.4273564119685562,
  'zero_crossing_rate_skew': 0.21029169116617238,
  'rms_max': 0.1901678,
  'rms_min': 0.068967745,
  'rms_mean': 0.11558959,
  'rms_std': 0.020466007,
  'rms_kurtosis': 0.33584242314380486,
  'rms_skew': 0.

In [8]:
df_features = pd.DataFrame(all_features)

In [9]:
df_features.shape

(999, 128)

In [10]:
df_features.head()

spectral_centroid_max  spectral_centroid_min  spectral_centroid_mean  \
0            5514.393296            1789.366583             3177.044739   
1            5626.545444            1763.465470             2850.278392   
2            4137.382271            1196.751465             2147.080162   
3            4141.859853            1554.571724             2700.604011   
4            6472.152579            2069.514147             3357.388867   

   spectral_centroid_std  spectral_centroid_kurtosis  spectral_centroid_skew  \
0             550.514460                    1.276833                0.851272   
1             450.497575                    7.135793                1.871643   
2             394.532048                    3.597655                1.475513   
3             411.344742                   -0.256947                0.124514   
4             548.511977                    1.316818                0.691419   

   spectral_rolloff_max  spectral_rolloff_min  spectral_rolloff_mean  \
0           9905.273438           4005.175781            6235.752497   
1          10314.404297           4155.908203            5927.176533   
2           7751.953125           2842.382812            4376.685986   
3           7708.886719           3531.445312            5177.960956   
4          10056.005859           4198.974609            6810.287667   

   spectral_rolloff_std  ...  mfcc_11_kurtosis  mfcc_11_skew  mfcc_12_max  \
0           1316.817640  ...         -0.381935     -0.087353    20.820358   
1            852.377153  ...         -0.121696      0.048562    19.133057   
2            842.405343  ...         -0.231261     -0.070840    11.926428   
3            678.921135  ...          0.151427     -0.124628    16.922087   
4            964.515301  ...         -0.134237      0.061878    23.652538   

   mfcc_12_min  mfcc_12_mean  mfcc_12_std  mfcc_12_kurtosis  mfcc_12_skew  \
0   -32.647717     -4.106478     8.183018          0.174437     -0.170466   
1   -32.525143    -10.891160     7.585576          0.191163      0.234933   
2   -40.928543    -14.242151     7.794230          0.155817     -0.128623   
3   -34.641380    -13.000867     6.993345          0.378246      0.133764   
4   -27.224190     -3.430558     7.447456          0.032957      0.119359   

        tempo  label  
0   95.703125  metal  
1  151.999081  metal  
2  112.347147  metal  
3   99.384014  metal  
4  135.999178  metal  

[5 rows x 128 columns]

In [11]:
df_features.to_csv('./all_features.csv', index=False)